---

# Exercise 1 異なるデータ、同じモデル

このコードでは、[ロジスティック回帰](https://ja.wikipedia.org/wiki/%E3%83%AD%E3%82%B8%E3%82%B9%E3%83%86%E3%82%A3%E3%83%83%E3%82%AF%E5%9B%9E%E5%B8%B0)を使用して、2種類のラベル付き文章データから感情を予測するモデルを作成します。

1. データの読み込みと確認
2. ロジスティック回帰でモデルを作成
3. モデルの動作確認

背景が灰色のセルはプログラムコードが記述されています。
`Shift` + `Enter` で実行してみましょう！

In [ ]:
#初期設定
import numpy as np
import MeCab
import spacy
nlp = spacy.load('en_core_web_sm')
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegression
from datasets import load_dataset

def parse_text(text):
    tagger = MeCab.Tagger()
    words = []
    for c in tagger.parse(text).splitlines()[:-1]:
        surface, feature = c.split('\t',1)
        pos = feature.split('\t')[3].split('-')[0]
        if pos == '名詞' or pos == '動詞':
            words.append(surface)
    return words

def filter_nouns_verbs(text):
    doc = nlp(text)
    return ' '.join([token.lemma_ for token in doc if token.pos_ in ("NOUN", "VERB")])

---
# 1. データの読み込みと確認

機械学習でよく使用されるプラットフォームの[Hugging Face](https://huggingface.co/)からデータを取得して表示します。

今回使用するのは製品レビュー文章と感情ラベルがセットになった`tyqiangz/multilingual-sentiments`です。

次のコードでは、日本語または英語の2種類データを読み込み、それぞれの先頭5行を表示します。  
データは、`"text"`に製品のレビュー、`"label"`に感情ラベルが格納されています。

感情ラベル
* $0$ ・・・ Positve
* $1$ ・・・ Neutral
* $2$ ・・・ Negative

In [ ]:
# データの読み込み
dataset_dict = {}
dataset_dict["jp"] = load_dataset("tyqiangz/multilingual-sentiments", "japanese").shuffle() # 日本語
dataset_dict["en"] = load_dataset("tyqiangz/multilingual-sentiments", "english").shuffle() # 英語

for language, dataset in dataset_dict.items():
    dataset.set_format(type="pandas")
    train_df = dataset["train"][:]
    print(language)
    display(train_df.head(5))

---
# 2. ロジスティック回帰でモデルを作成

読み込んだ２つのデータを、分類モデルの[ロジスティック回帰](https://ja.wikipedia.org/wiki/%E3%83%AD%E3%82%B8%E3%82%B9%E3%83%86%E3%82%A3%E3%83%83%E3%82%AF%E5%9B%9E%E5%B8%B0)で学習します。

日本語と英語は文法や文化が異なるため、処理も異なります。  
次のコードでは`parse_text`で日本語文章の処理、`filter_nouns_verbs`で英語文章の処理を行い、同じ学習モデル`LogisticRegression()`を使用しています。

In [ ]:
n = 1000
cv, lr = {}, {}
for lang in ["jp","en"]:
    print("Learning {%s} data by Logistic Regression..."%lang)
    documents = dataset_dict[lang]["train"]
    x = documents["text"][:n]
    y = documents["label"][:n]
    if lang == "jp":
        parsed_documents =  [" ".join(parse_text(line)) for line in x]
        doc_array = np.array(parsed_documents)
    else:
        filtered_texts = [filter_nouns_verbs(text) for text in x]
        doc_array = np.array(filtered_texts)        
    cv[lang] = CountVectorizer()
    x_bow = cv[lang].fit_transform(doc_array)
    lr[lang] = LogisticRegression()
    lr[lang].fit(x_bow, y)
    print("Done!")

---
# 3. モデルの動作確認

学習が完了しました。
`lr["jp"]`と`lr["en"]`

lr[mode].predict_proba()


次のセルを実行すると、`text`に入力された文章の感情分類の予測確率がモデル毎に表示されます。

In [ ]:
# 学習済みモデルによる感情分類
text = "コンパクトな仕様で使いやすく、剃り心地もよい。また、旅行の際の携帯に便利です。"

print("文章：", text)
for mode in ["jp", "en"]:
    if mode == "jp":
        print("日本語のデータで学習したモデルの予測値：")
        eval_text = cv[mode].transform(np.array([" ".join(parse_text(text))]))
    elif mode == "en":
        print("英語のデータで学習したモデルの予測値：")
        eval_text = cv[mode].transform(np.array([" ".join(filter_nouns_verbs(text))]))
    print(lr[mode].predict_proba(eval_text))

---
---

### 演習
1. `"コンパクトな仕様で使いやすく、剃り心地もよい。また、旅行の際の携帯に便利です。"`の予測分類は？
2. 日本語データで学習したモデルと英語データで学習したモデルで予測値が違うのはなぜだろうか。予測値の特徴から考察してみましょう。
3. `text=""`の文章を書き換えて、予測値の変化を観察してみましょう。
4. このモデルはどのような文章に対して使用するべきだろうか。
